In [36]:
import h5py
import numpy as np
import glob
from tqdm import tqdm
from astropy.time import Time

In [37]:
fnames = glob.glob('/work/yifan.wang/search-high-spin/prod3-fixsub/runs/*/*/full_data/*COMBINE*.hdf')

In [38]:
fnames.sort()

In [39]:
len(fnames)

84

In [40]:
ifar = [] #use exclusive ifar
tid = [] #template id, used to inquiry "MERGE" file's SNR etc. info
runs = [] #run/chunk name

ifos = ['H1','L1','V1']
time = {}
trig = {}
for i in ifos:
    time[i] = []
    trig[i] = []

for fname in tqdm(fnames):
    f = h5py.File(fname,'r')
    
    temp_name = fname.split('runs/')[1].split('/')
    #repeat the run/chunk len's times
    runs.append(np.repeat(temp_name[0]+'/'+temp_name[1],len(f['foreground/template_id'][:]))) 
    
    ifar.append(f['foreground/ifar'][:])
    tid.append(f['foreground/template_id'][:])
    
    for ifo in ifos:
        if ifo in f['foreground']:
            time[ifo].append(f['foreground'][ifo]['time'][:])
            trig[ifo].append(f['foreground'][ifo]['trigger_id'][:])
        else:
            time[ifo].append(np.ones(len(f['foreground/template_id'][:])) * -1)
            trig[ifo].append(np.ones(len(f['foreground/template_id'][:])) * -1)

100%|██████████████████████████████████████████████████████████████████████████████████████████████████████| 84/84 [00:02<00:00, 28.38it/s]


In [41]:
ifar = np.concatenate(ifar)
tid = np.concatenate(tid,dtype=int)
runs = np.concatenate(runs)

for ifo in ifos:
    time[ifo] = np.concatenate(time[ifo])
    trig[ifo] = np.concatenate(trig[ifo]).astype(int)

In [42]:
ifar

array([6.75339837e-07, 3.53711782e-06, 2.96372145e-06, ...,
       4.20252683e-06, 4.20252683e-06, 4.20252683e-06])

In [43]:
tid

array([  7542,  41511,  64436, ..., 256802, 660360, 250673])

In [44]:
runs

array(['O1/1', 'O1/1', 'O1/1', ..., 'O3b/9', 'O3b/9', 'O3b/9'],
      dtype='<U6')

In [45]:
len(ifar),len(tid),len(runs)

(1984759, 1984759, 1984759)

In [46]:
trig

{'H1': array([2722213017, 2685014330,  398713419, ...,         -1,         -1,
                -1]),
 'L1': array([2155043289, 2125602349,  315629738, ..., 1213577005, 1299808182,
        1288025709]),
 'V1': array([        -1,         -1,         -1, ..., 1158949890, 1241277299,
        1230021393])}

In [47]:
len(trig['H1']),len(trig['V1'])

(1984759, 1984759)

In [48]:
time

{'H1': array([ 1.12607353e+09,  1.12607355e+09,  1.12607356e+09, ...,
        -1.00000000e+00, -1.00000000e+00, -1.00000000e+00]),
 'L1': array([1.12607353e+09, 1.12607355e+09, 1.12607356e+09, ...,
        1.26125032e+09, 1.26125035e+09, 1.26125037e+09]),
 'V1': array([-1.00000000e+00, -1.00000000e+00, -1.00000000e+00, ...,
         1.26125032e+09,  1.26125035e+09,  1.26125037e+09])}

In [49]:
bank = h5py.File('/work/yifan.wang/search-high-spin/prod3-fixsub/runs/O3b/1/bank/H1L1V1-BANK2HDF-1257121340-427973.hdf','r')

# Rank

In [50]:
arg = np.argsort(ifar)[::-1]

In [51]:
arg

array([ 521307, 1544430, 1100229, ..., 1744424, 1738770, 1745161])

In [52]:
def get_name_from_time(h,l,v):
    '''
    h,l,v are end_time of Hanford, Livingston and Virgo, respectively
    use the average end time as the event's time
    '''
    time = 0
    i = 0
    for t in [h,l,v]:
        if t!=-1:
            time += t
            i+=1
    dt = Time(time/i,scale='utc', format='gps').datetime
    name = '{:02d}{:02d}{:02d}\_{:02d}{:02d}{:02d}'.format(dt.year - 2000,
                                                          dt.month,
                                                          dt.day, dt.hour,
                                                          dt.minute, dt.second)
    return name

In [53]:
print('name ifar mass1 mass2 spin1z spin2z snrH1 snrL1 snrV1')
for i,idx in enumerate(arg[:7]):#print the first seven events
    thisrun = runs[idx]#idx is the arguments index
    path = '/work/yifan.wang/search-high-spin/prod3-fixsub/runs/'+str(thisrun)+'/full_data/'
    snr = {}
    for ifo in ['H1','L1','V1']:
        this_trig_id = trig[ifo][idx]
        if this_trig_id != -1:
            fpath = glob.glob(path + ifo + '*MERGE*.hdf')#trigger id's info is in *MERGE*.hdf
            f = h5py.File(fpath[0],'r')[ifo]
            snr[ifo] = f['snr'][int(this_trig_id)]
        else:
            snr[ifo] = np.nan
    print(get_name_from_time(time['H1'][idx],time['L1'][idx],time['V1'][idx]),
          '%.2f' % ifar[idx],
          '%.2f %.2f %.2f %.2f' % (bank['mass1'][tid[idx]],bank['mass2'][tid[idx]],
          bank['spin1z'][tid[idx]],bank['spin2z'][tid[idx]]),runs[idx],
         '%.2f %.2f %.2f' % (snr['H1'],snr['L1'],snr['V1']))

name ifar mass1 mass2 spin1z spin2z snrH1 snrL1 snrV1
170817\_124104 21082.84 1.66 1.15 0.09 -0.09 O2/21 18.39 25.98 nan
200115\_042309 3761.76 4.88 1.88 -0.40 -0.17 O3b/15 6.33 8.90 nan
190417\_090325 0.98 1.12 1.08 0.33 -0.84 O3/2 6.34 6.90 nan
190929\_140800 0.29 1.01 1.00 0.01 -0.38 O3/23 5.25 7.06 nan
190519\_053312 0.28 1.77 1.25 0.72 0.63 O3/6 7.38 nan 5.36
191116\_140156 0.17 1.24 1.12 0.72 0.73 O3b/2 nan 6.27 6.44
170721\_064738 0.14 4.22 1.89 0.63 0.47 O2/18 5.39 7.06 nan


In [30]:
for i,idx in enumerate(arg[:7]):#print the first seven events
    thisrun = runs[idx]#idx is the arguments index
    path = '/work/yifan.wang/search-high-spin/prod3-fixsub/runs/'+str(thisrun)+'/full_data/'
    snr = {}
    for ifo in ['H1','L1','V1']:
        this_trig_id = trig[ifo][idx]
        if this_trig_id != -1:
            fpath = glob.glob(path + ifo + '*MERGE*.hdf')
            f = h5py.File(fpath[0],'r')[ifo]
            snr[ifo] = f['snr'][int(this_trig_id)]
        else:
            snr[ifo] = np.nan
    print(get_name_from_time(time['H1'][idx],time['L1'][idx],time['V1'][idx]),
          '& %.2f' % ifar[idx],
          '& %.2f & %.2f & %.2f & %.2f' % (bank['mass1'][tid[idx]],bank['mass2'][tid[idx]],
          bank['spin1z'][tid[idx]],bank['spin2z'][tid[idx]]),
         '& %.2f & %.2f & %.2f \\\\' % (snr['H1'],snr['L1'],snr['V1']))

170817\_124104 & 17326.85 & 1.66 & 1.15 & 0.09 & -0.09 & 18.39 & 25.98 & nan \\
200115\_042309 & 3058.95 & 4.88 & 1.88 & -0.40 & -0.17 & 6.33 & 8.90 & nan \\
190417\_090325 & 1.01 & 1.12 & 1.08 & 0.33 & -0.84 & 6.34 & 6.90 & nan \\
190519\_053312 & 0.29 & 1.77 & 1.25 & 0.72 & 0.63 & 7.38 & nan & 5.36 \\
190929\_140800 & 0.29 & 1.01 & 1.00 & 0.01 & -0.38 & 5.25 & 7.06 & nan \\
191116\_140156 & 0.18 & 1.24 & 1.12 & 0.72 & 0.73 & nan & 6.27 & 6.44 \\
170721\_064738 & 0.14 & 4.22 & 1.89 & 0.63 & 0.47 & 5.39 & 7.06 & nan \\
